# Pipeline Test 

In [1]:
import tensorflow_model_analysis as tfma
from tfx import v1 as tfx
import os

from tfx.components import CsvExampleGen
from tfx.components import Evaluator
from tfx.components import ExampleValidator
from tfx.components import Pusher
from tfx.components import SchemaGen
from tfx.components import StatisticsGen
from tfx.components import Trainer
from tfx.components import Transform
from tfx.dsl.components.common import resolver
from tfx.dsl.experimental import latest_blessed_model_resolver
# from models import features
from tfx.orchestration import pipeline
from tfx.proto import pusher_pb2
from tfx.proto import trainer_pb2
from tfx.types import Channel
from tfx.types.standard_artifacts import Model
from tfx.types.standard_artifacts import ModelBlessing
from ml_metadata.proto import metadata_store_pb2

import tensorflow_data_validation as tfdv

from tfx.orchestration.experimental.interactive.interactive_context import InteractiveContext
%load_ext tfx.orchestration.experimental.interactive.notebook_extensions.skip

## Defining Variables 

In [2]:
data_path=os.path.join('/text-classifier/Text-Classifer/ml/',"data")
data_path

'/text-classifier/Text-Classifer/ml/data'

In [3]:
context = InteractiveContext()

##  Example Gen

In [16]:
example_gen = CsvExampleGen(input_base=data_path)
context.run(example_gen)

ExecutionResult(
    component_id: CsvExampleGen
    execution_id: 1
    outputs:
        examples: Channel(
            type_name: Examples
            artifacts: [Artifact(artifact: id: 1
        type_id: 5
        uri: "/tmp/tfx-interactive-2021-06-11T15_19_33.490095-zinnjs06/CsvExampleGen/examples/1"
        properties {
          key: "split_names"
          value {
            string_value: "[\"train\", \"eval\"]"
          }
        }
        custom_properties {
          key: "input_fingerprint"
          value {
            string_value: "split:single_split,num_files:1,total_bytes:65862309,xor_checksum:1623155755,sum_checksum:1623155755"
          }
        }
        custom_properties {
          key: "payload_format"
          value {
            string_value: "FORMAT_TF_EXAMPLE"
          }
        }
        custom_properties {
          key: "span"
          value {
            int_value: 0
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        custom_properties {
          key: "tfx_version"
          value {
            string_value: "0.30.0"
          }
        }
        state: LIVE
        , artifact_type: id: 5
        name: "Examples"
        properties {
          key: "span"
          value: INT
        }
        properties {
          key: "split_names"
          value: STRING
        }
        properties {
          key: "version"
          value: INT
        }
        )]
            additional_properties: {}
            additional_custom_properties: {}
        ))

## Statistics Gen

In [17]:
statistics_gen = StatisticsGen(examples=example_gen.outputs["examples"])
context.run(statistics_gen)

ExecutionResult(
    component_id: StatisticsGen
    execution_id: 2
    outputs:
        statistics: Channel(
            type_name: ExampleStatistics
            artifacts: [Artifact(artifact: id: 2
        type_id: 7
        uri: "/tmp/tfx-interactive-2021-06-11T15_19_33.490095-zinnjs06/StatisticsGen/statistics/2"
        properties {
          key: "split_names"
          value {
            string_value: "[\"train\", \"eval\"]"
          }
        }
        custom_properties {
          key: "name"
          value {
            string_value: "statistics"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "StatisticsGen"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        custom_properties {
          key: "tfx_version"
          value {
            string_value: "0.30.0"
          }
        }
        state: LIVE
        , artifact_type: id: 7
        name: "ExampleStatistics"
        properties {
          key: "span"
          value: INT
        }
        properties {
          key: "split_names"
          value: STRING
        }
        )]
            additional_properties: {}
            additional_custom_properties: {}
        ))

In [20]:
context.show(statistics_gen.outputs['statistics'])

In [10]:
stats = tfdv.generate_statistics_from_csv(data_location=(data_path+'/data.csv'),delimiter=',')
stats

datasets {
  num_examples: 50000
  features {
    type: STRING
    string_stats {
      common_stats {
        num_non_missing: 50000
        min_num_values: 1
        max_num_values: 1
        avg_num_values: 1.0
        num_values_histogram {
          buckets {
            low_value: 1.0
            high_value: 1.0
            sample_count: 5000.0
          }
          buckets {
            low_value: 1.0
            high_value: 1.0
            sample_count: 5000.0
          }
          buckets {
            low_value: 1.0
            high_value: 1.0
            sample_count: 5000.0
          }
          buckets {
            low_value: 1.0
            high_value: 1.0
            sample_count: 5000.0
          }
          buckets {
            low_value: 1.0
            high_value: 1.0
            sample_count: 5000.0
          }
          buckets {
            low_value: 1.0
            high_value: 1.0
            sample_count: 5000.0
          }
          buckets {
            low

In [12]:
tfdv.visualize_statistics(lhs_statistics=stats)

## Schema Gen 

In [18]:
schema_gen = SchemaGen(statistics=statistics_gen.outputs["statistics"],infer_feature_shape=True)
context.run(schema_gen)

ExecutionResult(
    component_id: SchemaGen
    execution_id: 3
    outputs:
        schema: Channel(
            type_name: Schema
            artifacts: [Artifact(artifact: id: 3
        type_id: 9
        uri: "/tmp/tfx-interactive-2021-06-11T15_19_33.490095-zinnjs06/SchemaGen/schema/3"
        custom_properties {
          key: "name"
          value {
            string_value: "schema"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "SchemaGen"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        custom_properties {
          key: "tfx_version"
          value {
            string_value: "0.30.0"
          }
        }
        state: LIVE
        , artifact_type: id: 9
        name: "Schema"
        )]
            additional_properties: {}
            additional_custom_properties: {}
        ))

In [21]:
context.show(schema_gen.outputs['schema'])

Type  Presence Valency Domain
Feature name                                
'review'      BYTES  required              -
'sentiment'     INT  required              -

In [13]:
schema = tfdv.infer_schema(stats)
tfdv.display_schema(schema)

Type  Presence Valency Domain
Feature name                                
'review'      BYTES  required              -
'sentiment'     INT  required              -

## Example Validator

In [19]:
example_validator = ExampleValidator(
    statistics=statistics_gen.outputs["statistics"],
    schema=schema_gen.outputs["schema"]
)
context.run(example_validator)

ExecutionResult(
    component_id: ExampleValidator
    execution_id: 4
    outputs:
        anomalies: Channel(
            type_name: ExampleAnomalies
            artifacts: [Artifact(artifact: id: 4
        type_id: 11
        uri: "/tmp/tfx-interactive-2021-06-11T15_19_33.490095-zinnjs06/ExampleValidator/anomalies/4"
        properties {
          key: "split_names"
          value {
            string_value: "[\"train\", \"eval\"]"
          }
        }
        custom_properties {
          key: "name"
          value {
            string_value: "anomalies"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "ExampleValidator"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        custom_properties {
          key: "tfx_version"
          value {
            string_value: "0.30.0"
          }
        }
        state: LIVE
        , artifact_type: id: 11
        name: "ExampleAnomalies"
        properties {
          key: "span"
          value: INT
        }
        properties {
          key: "split_names"
          value: STRING
        }
        )]
            additional_properties: {}
            additional_custom_properties: {}
        ))

In [23]:
context.show(example_validator.ouputs['output'])

AttributeError: 'ExampleValidator' object has no attribute 'ouputs'

In [15]:
tfdv.validate_statistics(statistics=stats, schema=schema)

baseline {
  feature {
    name: "review"
    type: BYTES
    presence {
      min_fraction: 1.0
      min_count: 1
    }
    shape {
      dim {
        size: 1
      }
    }
  }
  feature {
    name: "sentiment"
    type: INT
    bool_domain {
    }
    presence {
      min_fraction: 1.0
      min_count: 1
    }
    shape {
      dim {
        size: 1
      }
    }
  }
}
anomaly_name_format: SERIALIZED_PATH